In [1]:
#%load_ext sparksql_magic
from pyspark.sql import SparkSession
from pyspark.sql.functions import expr, col

spark = SparkSession.builder.appName("dim_repo").config("spark.executor.memory", "1g").getOrCreate()

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/03/15 23:50:07 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [2]:
for key, value in spark.sparkContext.getConf().getAll():
    if "memory" in key or "executor" in key:
        print(f"{key} = {value}")

spark.executor.memory = 1g
spark.executor.id = driver
spark.executor.extraJavaOptions = -Djava.net.preferIPv6Addresses=false -XX:+IgnoreUnrecognizedVMOptions --add-opens=java.base/java.lang=ALL-UNNAMED --add-opens=java.base/java.lang.invoke=ALL-UNNAMED --add-opens=java.base/java.lang.reflect=ALL-UNNAMED --add-opens=java.base/java.io=ALL-UNNAMED --add-opens=java.base/java.net=ALL-UNNAMED --add-opens=java.base/java.nio=ALL-UNNAMED --add-opens=java.base/java.util=ALL-UNNAMED --add-opens=java.base/java.util.concurrent=ALL-UNNAMED --add-opens=java.base/java.util.concurrent.atomic=ALL-UNNAMED --add-opens=java.base/jdk.internal.ref=ALL-UNNAMED --add-opens=java.base/sun.nio.ch=ALL-UNNAMED --add-opens=java.base/sun.nio.cs=ALL-UNNAMED --add-opens=java.base/sun.security.action=ALL-UNNAMED --add-opens=java.base/sun.util.calendar=ALL-UNNAMED --add-opens=java.security.jgss/sun.security.krb5=ALL-UNNAMED -Djdk.reflect.useDirectMethodHandle=false


In [3]:
df = spark.read.json("/data/*.json.gz")
# Filter for IssuesEvent
df = df.filter(df["type"] == "IssuesEvent")
df = df.select(
    col("actor"),
    col("created_at"),
    col("id").alias("event_id"),
    col("org"),
    col("repo"),
    col("payload.action"),
    col("payload.issue")
)
df.createOrReplaceTempView("df")

25/03/15 23:50:31 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


## For github repo dim data


In [10]:
%%sql
MERGE INTO iceberg.dim_repo AS target USING (
  SELECT DISTINCT
    CAST(repo.id AS BIGINT) AS id,
    repo.name,
    repo.url
  FROM
    df
) AS source ON target.id = source.id WHEN MATCHED THEN
UPDATE
SET
  target.name = source.name,
  target.url = source.url WHEN NOT MATCHED THEN INSERT *;

25/03/15 23:18:08 ERROR Utils: Aborting task===================>  (22 + 1) / 23]
org.apache.spark.SparkRuntimeException: [MERGE_CARDINALITY_VIOLATION] The ON search condition of the MERGE statement matched a single row from the target table with multiple rows of the source table.
This could result in the target row being operated on more than once with an update or delete operation and is not allowed.
	at org.apache.spark.sql.errors.QueryExecutionErrors$.mergeCardinalityViolationError(QueryExecutionErrors.scala:2702)
	at org.apache.spark.sql.execution.datasources.v2.MergeRowsExec$BitmapCardinalityValidator.validate(MergeRowsExec.scala:164)
	at org.apache.spark.sql.execution.datasources.v2.MergeRowsExec$MergeRowIterator.next(MergeRowsExec.scala:203)
	at org.apache.spark.sql.execution.datasources.v2.MergeRowsExec$MergeRowIterator.next(MergeRowsExec.scala:176)
	at scala.collection.Iterator$$anon$12.hasNext(Iterator.scala:514)
	at org.apache.spark.sql.catalyst.expressions.GeneratedClass$Ge

Py4JJavaError: An error occurred while calling o36.sql.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 70.0 failed 1 times, most recent failure: Lost task 0.0 in stage 70.0 (TID 238) (485956c35f3e executor driver): org.apache.spark.SparkRuntimeException: [MERGE_CARDINALITY_VIOLATION] The ON search condition of the MERGE statement matched a single row from the target table with multiple rows of the source table.
This could result in the target row being operated on more than once with an update or delete operation and is not allowed.
	at org.apache.spark.sql.errors.QueryExecutionErrors$.mergeCardinalityViolationError(QueryExecutionErrors.scala:2702)
	at org.apache.spark.sql.execution.datasources.v2.MergeRowsExec$BitmapCardinalityValidator.validate(MergeRowsExec.scala:164)
	at org.apache.spark.sql.execution.datasources.v2.MergeRowsExec$MergeRowIterator.next(MergeRowsExec.scala:203)
	at org.apache.spark.sql.execution.datasources.v2.MergeRowsExec$Merge

In [6]:
%%sql 
SELECT
  *
FROM
  iceberg.dim_repo

+-----------+--------------------------------------------------------+-------------------------------------------------------------------------------------+
|        id |                                                   name |                                                                                 url |
+-----------+--------------------------------------------------------+-------------------------------------------------------------------------------------+
| 716240168 |                          AshwinAnand868/car-rental-app |                          https://api.github.com/repos/AshwinAnand868/car-rental-app |
| 291473513 |                VolkovLabs/volkovlabs-dynamictext-panel |                https://api.github.com/repos/VolkovLabs/volkovlabs-dynamictext-panel |
| 704981549 |                                  rainflame/pika-routes |                                  https://api.github.com/repos/rainflame/pika-routes |
| 103769370 |                                        rvlenth/emmeans |                                        https://api.github.com/repos/rvlenth/emmeans |
| 582137397 |                        ASJordi/website-activity-status |                        https://api.github.com/repos/ASJordi/website-activity-status |
|  67305738 |                                            dtolnay/syn |                                            https://api.github.com/repos/dtolnay/syn |
| 713640829 |                                          eryjus/16bcfs |                                          https://api.github.com/repos/eryjus/16bcfs |
| 619931831 |                                      wlky-0106/upptime |                                      https://api.github.com/repos/wlky-0106/upptime |
|  35810174 |  electron-react-boilerplate/electron-react-boilerplate |  https://api.github.com/repos/electron-react-boilerplate/electron-react-boilerplate |
| 736471558 |                               DanielKim7305/first_repo |                               https://api.github.com/repos/DanielKim7305/first_repo |
| 671269505 |                                        BerriAI/litellm |                                        https://api.github.com/repos/BerriAI/litellm |
| 589055547 |                           chickensoft-games/SuperNodes |                           https://api.github.com/repos/chickensoft-games/SuperNodes |
| 559150595 |                                          emoss08/Monta |                                          https://api.github.com/repos/emoss08/Monta |
| 228040072 |                hyttysmyrkky/node-red-contrib-vestel-tv |                https://api.github.com/repos/hyttysmyrkky/node-red-contrib-vestel-tv |
| 315330275 |                                    n00mkrad/flowframes |                                    https://api.github.com/repos/n00mkrad/flowframes |
| 266574355 |                                      Enubia/ghost-chat |                                      https://api.github.com/repos/Enubia/ghost-chat |
| 646659981 |                 nicedouble/StreamlitAntdComponentsDemo |                 https://api.github.com/repos/nicedouble/StreamlitAntdComponentsDemo |
| 312702579 |                 theepiccode/Awesome-CyberSec-Resources |                 https://api.github.com/repos/theepiccode/Awesome-CyberSec-Resources |
| 664620196 |         UMC-CommonPlant/CommonPlant-Server-Refactoring |         https://api.github.com/repos/UMC-CommonPlant/CommonPlant-Server-Refactoring |
| 202436160 |                                    blackjid/k8s-gitops |                                    https://api.github.com/repos/blackjid/k8s-gitops |
| 736076870 |                                   Colpr/Elike-mainsite |                                   https://api.github.com/repos/Colpr/Elike-mainsite |
| 320758273 |                                 goorm-dev/goorm-status |                                 https://api.github.com/repos/goorm-dev/goorm-status |
| 161012019 |                                      jellyfin/jellyfin |     

## For github organization data

In [7]:
%%sql
SELECT
  org.*
FROM
  df

+----------------------------------------------------+-------------+-----------+------------------------------------+----------------------------------------------------------------+
|                                         avatar_url | gravatar_id |        id |                              login |                                                            url |
+----------------------------------------------------+-------------+-----------+------------------------------------+----------------------------------------------------------------+
|                                               None |        None |      None |                               None |                                                           None |
|                                               None |        None |      None |                               None |                                                           None |
|                                               None |        None |      None |                               None |                                                           None |
|                                               None |        None |      None |                               None |                                                           None |
|                                               None |        None |      None |                               None |                                                           None |
|                                               None |        None |      None |                               None |                                                           None |
|                                               None |        None |      None |                               None |                                                           None |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.github.com/orgs/iptv-org |
|  https://avatars.githubusercontent.com/u/55937028? |             |  55937028 |                           iptv-org |                           https://api.g

In [9]:
%%sql
MERGE INTO iceberg.dim_org AS target USING (
  SELECT DISTINCT
    CAST(org.id AS BIGINT) AS id,
    org.login AS name,
    org.url
  FROM
    df
  WHERE
    org.id IS NOT NULL
) AS source ON target.id = source.id WHEN MATCHED THEN
UPDATE
SET
  target.name = source.name,
  target.url = source.url WHEN NOT MATCHED THEN INSERT *;

++
||
++
++

In [11]:
%%sql
SELECT
  *
FROM
  iceberg.dim_org

+--------+--------------------------+------------------------------------------------------+
|     id |                     name |                                                  url |
+--------+--------------------------+------------------------------------------------------+
|   4223 |                    rails |                    https://api.github.com/orgs/rails |
|   6183 |               thoughtbot |               https://api.github.com/orgs/thoughtbot |
|   8085 |                  Shopify |                  https://api.github.com/orgs/Shopify |
|   9919 |                   github |                   https://api.github.com/orgs/github |
|  10060 |                  vertica |                  https://api.github.com/orgs/vertica |
|  10757 |                   puzzle |                   https://api.github.com/orgs/puzzle |
|  13131 |                 basecamp |                 https://api.github.com/orgs/basecamp |
|  18133 |                      git |                      https://api.github.com/orgs/git |
|  20768 |                  zencart |                  https://api.github.com/orgs/zencart |
|  21210 |              textpattern |              https://api.github.com/orgs/textpattern |
|  21640 |                    quran |                    https://api.github.com/orgs/quran |
|  23900 |                      box |                      https://api.github.com/orgs/box |
|  25158 |                      php |                      https://api.github.com/orgs/php |
|  27804 |                   django |                   https://api.github.com/orgs/django |
|  43271 |              revelrylabs |              https://api.github.com/orgs/revelrylabs |
|  47359 |                   apache |                   https://api.github.com/orgs/apache |
|  54555 |                biopython |                https://api.github.com/orgs/biopython |
|  56974 |                  eclipse |                  https://api.github.com/orgs/eclipse |
|  64846 |                   groovy |                   https://api.github.com/orgs/groovy |
|  68587 |                cosmocode |                https://api.github.com/orgs/cosmocode |
|  69631 |                 facebook |                 https://api.github.com/orgs/facebook |
|  70142 |                   jquery |                   https://api.github.com/orgs/jquery |
|  71971 |                   openid |                   https://api.github.com/orgs/openid |
|  80138 |                    rgd87 |                    https://api.github.com/orgs/rgd87 |
|  80584 |                    antlr |                    https://api.github.com/orgs/antlr |
|  81121 |                pymc-devs |                https://api.github.com/orgs/pymc-devs |
|  82592 |                   square |                   https://api.github.com/orgs/square |
|  83798 |                 globocom |                 https://api.github.com/orgs/globocom |
|  86724 |               processone |               https://api.github.com/orgs/processone |
|  87549 |                  Kitware |                  https://api.github.com/orgs/Kitware |
|  96669 |                 rabbitmq |                 https://api.github.com/orgs/rabbitmq |
|  97652 |                  infinum |                  https://api.github.com/orgs/infinum |
| 104378 |               virtualmin |               https://api.github.com/orgs/virtualmin |
| 107184 |                linuxmint |                https://api.github.com/orgs/linuxmint |
| 107424 |                jenkinsci |                https://api.github.com/orgs/jenkinsci |
| 109777 |                   zeromq |                   https://api.github.com/orgs/zeromq |
| 119815 |                  tinymce |                  https://api.github.com/orgs/tinymce |
| 124156 |                   gradle |                   https://api.github.com/orgs/gradle |
| 130493 |          internetarchive |          https://api.github.com/orgs/internetarchive |
| 131524 |                  mozilla |                  https://api.github.com/orgs/mozilla |
|

## TBD: dim_user(actor), fct_issue_events (github issue events), dim_issues

In [13]:
%%sql
SELECT
  *
FROM
  df

+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+----------------------+-------------+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------+--------+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [21]:
%%sql
SELECT
  -- Primary Key & Event Type
  CAST(event_id AS BIGINT) AS event_id,       -- Unique event ID
  action,                                     -- Event type (created, closed, reopened)

  -- Issue Features (ML Inputs)
  issue.title AS issue_title,                 -- Issue title
  issue.body AS issue_body,                   -- Issue description
  issue.author_association,                   -- Creator's association
  issue.state AS issue_state,                 -- Current state (open, closed)
  issue.state_reason AS issue_state_reason,   -- Reason for state change
  issue.user AS issue_creator,                -- Creator of the issue
  issue.comments AS issue_comment_count,      -- Number of comments (could be useful)
  issue.reactions,                            -- User reactions (could be useful)
  issue.assignee,                             -- Single assignee (Maybe useful)
  issue.assignees,                            -- Multiple assignees (Maybe useful)
  issue.labels,                               -- Labels (Maybe useful)
  issue.milestone,                            -- Milestone (Maybe useful)

  -- Timestamps (Time-Based Features)
  CAST(issue.created_at AS TIMESTAMP) AS issue_created_at, 
  CAST(issue.closed_at AS TIMESTAMP) AS issue_closed_at, 
  CAST(issue.updated_at AS TIMESTAMP) AS issue_updated_at, 
  CAST(created_at AS TIMESTAMP) AS event_created_at, -- Timestamp when event occurred

  -- Foreign Keys (For Joins, Placed at the End)
  CAST(issue.id AS BIGINT) AS issue_id,       -- FK to Issues
  CAST(actor.id AS BIGINT) AS user_id,        -- FK to Users
  CAST(org.id AS BIGINT) AS org_id            -- FK to Organizations

FROM df;

ParseException: 
[PARSE_SYNTAX_ERROR] Syntax error at or near '('.(line 1, pos 15)

== SQL ==
DESCRIBE TABLE (
---------------^^^
SELECT
  -- Primary Key & Event Type
  CAST(event_id AS BIGINT) AS event_id,       -- Unique event ID
  action,                                     -- Event type (created, closed, reopened)

  -- Issue Features (ML Inputs)
  issue.title AS issue_title,                 -- Issue title
  issue.body AS issue_body,                   -- Issue description
  issue.author_association,                   -- Creator's association
  issue.state AS issue_state,                 -- Current state (open, closed)
  issue.state_reason AS issue_state_reason,   -- Reason for state change
  issue.user AS issue_creator,                -- Creator of the issue
  issue.comments AS issue_comment_count,      -- Number of comments (could be useful)
  issue.reactions,                            -- User reactions (could be useful)
  issue.assignee,                             -- Single ass

In [4]:
%%sql
INSERT OVERWRITE iceburg.fct_issue_event 
SELECT
  CAST(event_id AS BIGINT) AS event_id,
  action,
  issue.title AS issue_title,
  issue.body AS issue_body,
  issue.author_association,
  issue.state AS issue_state,
  issue.state_reason AS issue_state_reason,
  issue.user AS issue_creator,
  issue.comments AS issue_comment_count,
  issue.reactions,
  issue.assignee,
  issue.assignees,
  issue.labels,
  issue.milestone,
  CAST(issue.created_at AS TIMESTAMP) AS issue_created_at,
  CAST(issue.closed_at AS TIMESTAMP) AS issue_closed_at,
  CAST(issue.updated_at AS TIMESTAMP) AS issue_updated_at,
  CAST(created_at AS TIMESTAMP) AS event_created_at,
  CAST(issue.id AS BIGINT) AS issue_id,
  CAST(actor.id AS BIGINT) AS user_id,
  CAST(org.id AS BIGINT) AS org_id
FROM df
WHERE DATE(CAST(created_at AS TIMESTAMP)) = '2024-01-01'; 

25/03/15 23:50:42 WARN SparkSession: Using an existing Spark session; only runtime SQL configurations will take effect.
                                                                                

++
||
++
++